# Import Statements

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import folium
from folium import plugins
from folium.plugins import HeatMap
from datetime import datetime
from datetime import timedelta
import math
import random
import timeit
import urllib.request, json # we will need urllib to communicate with the api and then json to read the data we get

---

# Bycicle Stations

## Retrieving bicycle stations in Duisburg

In [2]:
# we simply send the API the request parameter city with the corresponding city ids
# city IDs can be found here https://api.nextbike.net/maps/nextbike-live.json?list_cities=1
city_ids = ['131','132','133','137']
with urllib.request.urlopen("https://api.nextbike.net/maps/nextbike-live.json?city={}".format(','.join(city_ids))) as url:
    duisburg_stations_data = json.loads(url.read().decode())


In [3]:
# now we will go through the data, which is internally now stored as dictionary
# we will save all stations data in a list called duisburg_stations
# we also delete some key/value pairs, because they store lists, which will we cannot display in a dataframe
# notice that we only use stations, which have 'spot' set to true
# as stated in nextbikes API documentation this means that this data is indeed a stations
# places with 'spot' set to false, are locations where people left their bike unauthorised
duisburg_stations = []
for city in duisburg_stations_data['countries'][0]['cities']:
    for place in city['places']:
        if place['spot'] == True:
            duisburg_stations.append({
                'id': place['number'],
                'name': place['name'],
                'lat': place['lat'],
                'lon': place['lng'],
                'city': city['alias']
            })

In [4]:
duisburg_stations = pd.DataFrame(duisburg_stations)

In [5]:
duisburg_stations['coordinates'] = list(zip(duisburg_stations['lat'].round(4), duisburg_stations['lon'].round(4)))

In [6]:
duisburg_stations.set_index('id', inplace=True)
duisburg_stations.drop(['lat', 'lon'], axis=1, inplace=True)

In [7]:
duisburg = pd.read_pickle('../0_data/duisburg_clean.pkl')

In [8]:
duisburg_stations['city'].unique()

array(['bottrop', 'duisburg', 'essen', 'muelheim'], dtype=object)

In [9]:
Du_map = folium.Map(location=(51.44, 6.83), zoom_start=10, control_scale=True, max_zoom=20)
Du_map.add_child(plugins.HeatMap(duisburg["dest"], radius=15)) #adding heatmap points with the cleaned orig coordinates

color_mapping = {
    'bottrop': 'black',
    'duisburg': 'white',
    'essen': 'black',
    'muelheim': 'black'
}


for index, row in duisburg_stations.iterrows():
    color = color_mapping[row['city']]
    folium.CircleMarker(radius=5, location=row.coordinates, color=color, fill_color='black', popup=row['name'] + ' (' + row['city']+')').add_to(Du_map)
Du_map #showing Map

In [10]:
duisburg_stations.to_pickle('../0_data/stations/duisburg_stations.pkl')
duisburg_stations

name      city        coordinates
id                                                             
7201                  Hauptbahnhof   bottrop    (51.51, 6.9365)
7203                   Pferdemarkt   bottrop  (51.5347, 6.9569)
7202                Berliner Platz   bottrop   (51.523, 6.9264)
7204       Knappschaftskrankenhaus   bottrop  (51.5153, 6.9085)
7206           Ernst-Wilczok-Platz   bottrop  (51.5241, 6.9249)
...                            ...       ...                ...
7932             HRW Campus Styrum  muelheim  (51.4491, 6.8692)
7920  MWB / Friedrich-Ebert-Straße  muelheim   (51.428, 6.8794)
7927         HRW/Duisburger Straße  muelheim  (51.4271, 6.8578)
7934                  HRW/Parkhaus  muelheim  (51.4277, 6.8605)
7922              Bahnstraße / RS1  muelheim  (51.4297, 6.8775)

[143 rows x 3 columns]

## Retrieving bicycle stations in Duisburg

In [11]:

with urllib.request.urlopen("https://api.nextbike.net/maps/nextbike-live.json?city=438") as url:
    marburg_stations_data = json.loads(url.read().decode())

In [12]:
marburg_stations = []
for place in marburg_stations_data['countries'][0]['cities'][0]['places']:
    if place['spot'] == True:
            marburg_stations.append({
                'id': place['number'],
                'name': place['name'],
                'lat': place['lat'],
                'lon': place['lng']
            })

In [13]:
marburg_stations = pd.DataFrame(marburg_stations)
marburg_stations['coordinates'] = list(zip(marburg_stations['lat'].round(4), marburg_stations['lon'].round(4)))

In [14]:
marburg = pd.read_pickle('../0_data/marburg_clean.pkl')

In [15]:
Ma_map = folium.Map(location=(50.81, 8.74), zoom_start=10, control_scale=True, max_zoom=20)
Ma_map.add_child(plugins.HeatMap(marburg["orig"], radius=15)) #adding heatmap points with the cleaned orig coordinates

for index, row in marburg_stations.iterrows():
    folium.CircleMarker(radius=5, location=row.coordinates, color='black', fill_color='black', popup=row['name']).add_to(Ma_map)
    
    
Ma_map

In [16]:
# we drop all columns except for coordinates and number
# number is nextbikes internal id of a station, so we will use it as index
marburg_stations.drop(marburg_stations.columns.difference(['coordinates', 'id']), 1, inplace=True)
marburg_stations.set_index('id', inplace=True)

In [17]:
marburg_stations.to_pickle('../0_data/stations/marburg_stations.pkl')
marburg_stations

coordinates
id                     
5150  (50.8229, 8.7747)
5151  (50.7895, 8.7564)
5152   (50.8079, 8.767)
5153  (50.8058, 8.7828)
5154   (50.7784, 8.768)
5155   (50.8089, 8.773)
5156  (50.8132, 8.7759)
5157  (50.8166, 8.7515)
5158  (50.8081, 8.7754)
5159  (50.8043, 8.7701)
5160  (50.7856, 8.7794)
5162  (50.7988, 8.7621)
5163   (50.7987, 8.753)
5164  (50.8279, 8.7751)
5165    (50.82, 8.7737)
5166   (50.811, 8.7742)
5168  (50.8167, 8.7812)
5169  (50.8098, 8.7794)
5171  (50.8013, 8.7733)
5172  (50.7904, 8.7669)
5173  (50.7952, 8.7633)
5174   (50.7953, 8.762)
5175  (50.8038, 8.7747)
5176  (50.8071, 8.7699)
5177  (50.8362, 8.7568)
5178  (50.8047, 8.7592)
5147  (50.8128, 8.7806)
5145  (50.8137, 8.7707)
5144  (50.8147, 8.7712)
5146   (50.8202, 8.771)
5143  (50.7946, 8.7722)
5142  (50.8033, 8.7641)
5141   (50.814, 8.7662)
5140  (50.8161, 8.7722)